In [ ]:
## mercadolibre brand mapping
## Author : Nitin Bhayana 
## 10 June 2022
## version : 1.0

In [1]:

import numpy as np
from bs4 import BeautifulSoup


from tqdm.notebook import tqdm
import time

import pandas as pd
import psycopg2
import datetime

from selenium import webdriver
from selenium.webdriver.common.by import By
import requests
from selenium.webdriver.support.ui import WebDriverWait
import selenium.webdriver.support.expected_conditions as EC

from tqdm import tqdm
tqdm.pandas()
import time

headers = {"User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/93.0.4577.63 Safari/537.36",
           "Accept-Encoding": "gzip, deflate, br",
           "Accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.9",
           "DNT":"1",
           "Connection":"close",
           "Upgrade-Insecure-Requests": "1"}

class postgres_conn:
    def getConn(self):
        try:
            connection = psycopg2.connect(user='postgres',
                                          password='postgres_007',
                                          host="1.pgsql.db.1digitalstack.com",
                                          port='5432',
                                          database='postgres')

            cursor = connection.cursor()
            # Print PostgreSQL Connection properties
            print(connection.get_dsn_parameters(), "\n")

            # Print PostgreSQL version
            return cursor, connection

        except (Exception, psycopg2.Error) as error:
            print("Error while connecting to PostgreSQL", error)
            return error, error
    def getConn2(self):
        try:
            connection = psycopg2.connect(user='postgres',
                                          password='reporting_007',
                                          host="2.pgsql.db.1digitalstack.com",
                                          port='5432',
                                          database='postgres')

            cursor = connection.cursor()
            # Print PostgreSQL Connection properties
            print(connection.get_dsn_parameters(), "\n")

            # Print PostgreSQL version
            return cursor, connection

        except (Exception, psycopg2.Error) as error:
            print("Error while connecting to PostgreSQL", error)
            return error, error


    def close_connection(self, cursor, connection):
        # closing database connection.
        if(connection):
            cursor.close()
            connection.close()
            print("PostgreSQL connection is closed")
            
pg = postgres_conn()
conn = pg.getConn()
conn2 = pg.getConn2()

job_id=input("Enter keystone ids with comma.").split(",")
days=input(" Enter no of days for which data needs brand mapping.\n")
job_id.append("")
tuple(job_id)

query = f"""
select brand,title,sku,job_name,channel_id
from ready.serp_details smd join ready.serp_mongo_details m on m.serp_mongo_id=smd.serp_mongo_id
where smd.crawl_date > now() - interval '{days} day' and keystone_job_id in {tuple(job_id)}
"""
serp_details = pd.read_sql_query(query, conn[1])

rawdf=serp_details.drop_duplicates('sku')

rawdf1=rawdf

df_ASIN = rawdf1[["sku"]]
df_ASIN.dropna(inplace=True)
df_ASIN.drop_duplicates(inplace=True)
asinlist = list(df_ASIN['sku'])
len(asinlist)


query_2 = f""" 
Select channel_sku_id,country_code, brand_name, categories,category_id
from entity.product_master
where channel_sku_id in {tuple(asinlist)} 
"""

pm_data = pd.read_sql_query(query_2, conn[1])



mapped_df=pd.merge(rawdf1,pm_data, how='left', left_on=['sku'],right_on=['channel_sku_id'])
mapped_df

{'user': 'postgres', 'channel_binding': 'prefer', 'dbname': 'postgres', 'host': '1.pgsql.db.1digitalstack.com', 'port': '5432', 'options': '', 'sslmode': 'prefer', 'sslcompression': '0', 'sslsni': '1', 'ssl_min_protocol_version': 'TLSv1.2', 'gssencmode': 'disable', 'krbsrvname': 'postgres', 'target_session_attrs': 'any'} 

{'user': 'postgres', 'channel_binding': 'prefer', 'dbname': 'postgres', 'host': '2.pgsql.db.1digitalstack.com', 'port': '5432', 'options': '', 'sslmode': 'prefer', 'sslcompression': '0', 'sslsni': '1', 'ssl_min_protocol_version': 'TLSv1.2', 'gssencmode': 'disable', 'krbsrvname': 'postgres', 'target_session_attrs': 'any'} 

Enter keystone ids with comma.64dc5bdcb4c91129aaf4b3f4,64dc5eeeb4c91129aaf4be0e
 Enter no of days for which data needs brand mapping.
9


C:\Users\Administrator\AppData\Local\Temp\2\ipykernel_119216\3118012154.py:89: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  serp_details = pd.read_sql_query(query, conn[1])
C:\Users\Administrator\AppData\Local\Temp\2\ipykernel_119216\3118012154.py:96: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_ASIN.dropna(inplace=True)
C:\Users\Administrator\AppData\Local\Temp\2\ipykernel_119216\3118012154.py:97: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_ASIN.drop_dup

brand                                              title  \
0        None                     Wet N Wild Megaglo Blush Stick   
1        None                     Motorcraft 5w20 Original Oil S   
2     BENEFIT                      Benefit Benetint Lip Tint Ink   
3        None                          Precisely, My Brow Pencil   
4        None                            Nars Blush Blush Orgasm   
...       ...                                                ...   
7642     None  Motul 7100 4-Stroke Oil 10w40 Honda Yamaha Har...   
7643     None                     Motul 7100 10w40 Synthetic Oil   
7644     None  Tank Steering Odyssey 2011 2012 2013 2014 2015...   
7645     None  Oil 25w50 Raloy Diesel Multigrade Bucket 19 Li...   
7646     None              Oil 25w50 Multigrade Mineral 5 Liters   

                 sku                         job_name  channel_id  \
0     MLM-1910053821  Mercadolibre r.no.580 Serp_job           46   
1     MLM-1727324395  Mercadolibre r.no.581 Serp_job           46   
2        MLM20544742  Mercadolibre r.no.580 Serp_job           46   
3     MLM-1364875766  Mercadolibre r.no.580 Serp_job           46   
4     MLM-1463540739  Mercadolibre r.no.580 Serp_job           46   
...              ...                              ...         ...   
7642   MLM-946295758  Mercadolibre r.no.581 Serp_job           46   
7643  MLM-1382185204  Mercadolibre r.no.581 Serp_job           46   
7644   MLM-723499488  Mercadolibre r.no.581 Serp_job           46   
7645  MLM-1420944273  Mercadolibre r.no.581 Serp_job           46   
7646  MLM-1364192736  Mercadolibre r.no.581 Serp_job           46   

      channel_sku_id country_code brand_name categories category_id  
0                NaN          NaN        NaN        NaN         NaN  
1                NaN          NaN        NaN        NaN         NaN  
2                NaN          NaN        NaN        NaN         NaN  
3     MLM-1364875766           MX       None       None        None  
4                NaN          NaN        NaN        NaN         NaN  
...              ...          ...        ...        ...         ...  
7642             NaN          NaN        NaN        NaN         NaN  
7643             NaN          NaN        NaN        NaN         NaN  
7644             NaN          NaN        NaN        NaN         NaN  
7645  MLM-1420944273           MX      Raloy       None        None  
7646             NaN          NaN        NaN        NaN         NaN  

[7647 rows x 10 columns]

In [2]:
df2=mapped_df[mapped_df['categories'].isnull()][['channel_id','sku','title','brand_name']]
df2

channel_id             sku  \
0             46  MLM-1910053821   
1             46  MLM-1727324395   
2             46     MLM20544742   
3             46  MLM-1364875766   
4             46  MLM-1463540739   
...          ...             ...   
7642          46   MLM-946295758   
7643          46  MLM-1382185204   
7644          46   MLM-723499488   
7645          46  MLM-1420944273   
7646          46  MLM-1364192736   

                                                  title brand_name  
0                        Wet N Wild Megaglo Blush Stick        NaN  
1                        Motorcraft 5w20 Original Oil S        NaN  
2                         Benefit Benetint Lip Tint Ink        NaN  
3                             Precisely, My Brow Pencil       None  
4                               Nars Blush Blush Orgasm        NaN  
...                                                 ...        ...  
7642  Motul 7100 4-Stroke Oil 10w40 Honda Yamaha Har...        NaN  
7643                     Motul 7100 10w40 Synthetic Oil        NaN  
7644  Tank Steering Odyssey 2011 2012 2013 2014 2015...        NaN  
7645  Oil 25w50 Raloy Diesel Multigrade Bucket 19 Li...      Raloy  
7646              Oil 25w50 Multigrade Mineral 5 Liters        NaN  

[7591 rows x 4 columns]

In [3]:
asinlist = list(df2['sku'])
len(asinlist)

7591

In [4]:
batches=int(len(asinlist)/50 )+1
batches

152

In [5]:
asinlist

['MLM-1910053821',
 'MLM-1727324395',
 'MLM20544742',
 'MLM-1364875766',
 'MLM-1463540739',
 'MLM-768997261',
 'MLM-1917333545',
 'MLM-1784079925',
 'MLM-824640602',
 'MLM-824648265',
 'MLM-1600036334',
 'MLM-692618980',
 'MLM-824641655',
 'MLM-792957313',
 'MLM-1851198093',
 'MLM-718225655',
 'MLM-1890496059',
 'MLM-1887478629',
 'MLM-838312095',
 'MLM-1852795021',
 'MLM-2220085112',
 'MLM-1653821734',
 'MLM-1519009905',
 'MLM-692625184',
 'MLM-1912257733',
 'MLM-1905712144',
 'MLM-1896115433',
 'MLM-2148191208',
 'MLM-1329886079',
 'MLM-1791620133',
 'MLM-1829752812',
 'MLM-1378982893',
 'MLM-837818588',
 'MLM-1870702557',
 'MLM-802517082',
 'MLM-1577623054',
 'MLM-1700611120',
 'MLM-2028053672',
 'MLM-2394018214',
 'MLM-617965821',
 'MLM-1351534510',
 'MLM-2108353748',
 'MLM-1584234213',
 'MLM-1912710705',
 'MLM-555957744',
 'MLM-619767217',
 'MLM19914570',
 'MLM-929866433',
 'MLM-759318919',
 'MLM-1906067247',
 'MLM-625141977',
 'MLM-773200285',
 'MLM-1910562685',
 'MLM-929871319',

In [8]:
df=pd.DataFrame(columns=['channel_sku_id','brand_name','categories','sold'])
df

Empty DataFrame
Columns: [channel_sku_id, brand_name, categories, sold]
Index: []

In [9]:
for batch in tqdm(range(0,len(asinlist))):
    print(batch)
    for val in (range(batch*50,(batch*50)+50)):
        i=asinlist[val]
        print(batch,i)
        if "-" in i:
            #Url== "https://produto.mercadolibre.com.br/{}".format(i)
            Url = "https://articulo.mercadolibre.com.mx/{}".format(i)
        else:
            #Url="https://www.mercadolivre.com.br//p/{}".format(i)
            Url="https://www.mercadolibre.com.mx//p/{}".format(i)

        #Url = "https://produto.mercadolibre.com.br/{}".format(i)
        #Url = "https://articulo.mercadolibre.com.mx/{}".format(i)
        print(Url)
        value=''
        #s= get_session(proxies)
        r= requests.get(Url,headers=headers)

        soup=BeautifulSoup(r.content,'html.parser')

        try:
            main=soup.find('div',class_="ui-pdp-specs__table")
            labels=[labels.text for labels in main.find_all('th')]
            try:
                index=labels.index('Marca')
                value=soup.find_all('td')[index].text
                print(value)
            except:
                value= 'not available'
                print(value)
        except:
            pass

        try:
            main=soup.find('div',class_="ui-vpp-striped-specs")
            labels=[labels.text for labels in main.find_all('th')]
            try:
                index=labels.index('Marca')
                value=soup.find_all('td')[index].text
                print(value)
            except:
                value= 'not available'
                print(value)
        except:
            pass

        try:
            category=soup.find('div',class_="ui-pdp-breadcrumb")
            cats=[labels.text for labels in category.find_all('li')]
            print(cats)
        except:
            cats=[]

        try:
            sales=soup.find('div',class_='ui-pdp-header')
            d=sales.find('span',class_='ui-pdp-subtitle')
            sold=d.text
            print(sold)
        except:
            sold='na'
            print(sold)

        df1={'channel_sku_id': i, 'brand_name': value, 'categories': cats, 'sold':sold}
        df=df.append(df1, ignore_index = True)
    time.sleep(300)

  0%|                                                                                         | 0/7591 [00:00<?, ?it/s]

0
0 MLM-1910053821
https://articulo.mercadolibre.com.mx/MLM-1910053821
Wet n Wild
['Belleza y Cuidado Personal', 'Maquillaje', 'Rostro', 'Iluminadores y Rubores']
Nuevo  |  +25 vendidos
0 MLM-1727324395
https://articulo.mercadolibre.com.mx/MLM-1727324395


C:\Users\Administrator\AppData\Local\Temp\2\ipykernel_119216\3236900016.py:65: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df=df.append(df1, ignore_index = True)


na
0 MLM20544742
https://www.mercadolibre.com.mx//p/MLM20544742


C:\Users\Administrator\AppData\Local\Temp\2\ipykernel_119216\3236900016.py:65: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df=df.append(df1, ignore_index = True)


...

C:\Users\Administrator\AppData\Local\Temp\2\ipykernel_119216\3236900016.py:65: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df=df.append(df1, ignore_index = True)


Raloy
[]
Nuevo  |  +50 vendidos
151 MLM-1364192736
https://articulo.mercadolibre.com.mx/MLM-1364192736


C:\Users\Administrator\AppData\Local\Temp\2\ipykernel_119216\3236900016.py:65: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df=df.append(df1, ignore_index = True)
C:\Users\Administrator\AppData\Local\Temp\2\ipykernel_119216\3236900016.py:65: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df=df.append(df1, ignore_index = True)
  2%|█▍                                                                    | 151/7591 [20:19:21<1001:19:52, 484.52s/it]

Raloy
[]
Nuevo  |  +5 vendidos


IndexError: list index out of range

In [10]:
df

channel_sku_id  brand_name  \
0     MLM-1910053821  Wet n Wild   
1     MLM-1727324395               
2        MLM20544742     Benefit   
3     MLM-1364875766      BENFIT   
4     MLM-1463540739               
...              ...         ...   
7586   MLM-946295758       Motul   
7587  MLM-1382185204       Motul   
7588   MLM-723499488       Honda   
7589  MLM-1420944273       Raloy   
7590  MLM-1364192736       Raloy   

                                             categories  \
0     [Belleza y Cuidado Personal, Maquillaje, Rostr...   
1                                                    []   
2                                                    []   
3     [Belleza y Cuidado Personal, Maquillaje, Ojos,...   
4     [Belleza y Cuidado Personal, Maquillaje, Rostr...   
...                                                 ...   
7586                                                 []   
7587                                                 []   
7588                                                 []   
7589                                                 []   
7590                                                 []   

                         sold  
0      Nuevo  |  +25 vendidos  
1                          na  
2     Nuevo  |  +100 vendidos  
3     Nuevo  |  +100 vendidos  
4        Nuevo  |  2 vendidos  
...                       ...  
7586     Nuevo  |  3 vendidos  
7587  Nuevo  |  +100 vendidos  
7588  Nuevo  |  +100 vendidos  
7589   Nuevo  |  +50 vendidos  
7590    Nuevo  |  +5 vendidos  

[7591 rows x 4 columns]

In [ ]:
df.info()

In [11]:
final1=pd.merge(rawdf1,df,left_on='sku', right_on='channel_sku_id', how= 'right')
final=final1[['sku','title','brand_name','categories','sold']]

In [12]:
final

sku                                              title  \
0     MLM-1910053821                     Wet N Wild Megaglo Blush Stick   
1     MLM-1727324395                     Motorcraft 5w20 Original Oil S   
2        MLM20544742                      Benefit Benetint Lip Tint Ink   
3     MLM-1364875766                          Precisely, My Brow Pencil   
4     MLM-1463540739                            Nars Blush Blush Orgasm   
...              ...                                                ...   
7586   MLM-946295758  Motul 7100 4-Stroke Oil 10w40 Honda Yamaha Har...   
7587  MLM-1382185204                     Motul 7100 10w40 Synthetic Oil   
7588   MLM-723499488  Tank Steering Odyssey 2011 2012 2013 2014 2015...   
7589  MLM-1420944273  Oil 25w50 Raloy Diesel Multigrade Bucket 19 Li...   
7590  MLM-1364192736              Oil 25w50 Multigrade Mineral 5 Liters   

      brand_name                                         categories  \
0     Wet n Wild  [Belleza y Cuidado Personal, Maquillaje, Rostr...   
1                                                                []   
2        Benefit                                                 []   
3         BENFIT  [Belleza y Cuidado Personal, Maquillaje, Ojos,...   
4                 [Belleza y Cuidado Personal, Maquillaje, Rostr...   
...          ...                                                ...   
7586       Motul                                                 []   
7587       Motul                                                 []   
7588       Honda                                                 []   
7589       Raloy                                                 []   
7590       Raloy                                                 []   

                         sold  
0      Nuevo  |  +25 vendidos  
1                          na  
2     Nuevo  |  +100 vendidos  
3     Nuevo  |  +100 vendidos  
4        Nuevo  |  2 vendidos  
...                       ...  
7586     Nuevo  |  3 vendidos  
7587  Nuevo  |  +100 vendidos  
7588  Nuevo  |  +100 vendidos  
7589   Nuevo  |  +50 vendidos  
7590    Nuevo  |  +5 vendidos  

[7591 rows x 5 columns]

In [7]:
request_no=input("Enter the request number of the requests seperated with underscore(_) ")
#547_552
file='final_output_mercadolibre_mexico_{}.xlsx'.format(request_no)

Enter the request number of the requests seperated with underscore(_) 580_581


In [13]:
final.to_excel(file)

In [15]:
import smtplib
from email.mime.text import MIMEText
from email.mime.multipart import MIMEMultipart
from email.mime.base import MIMEBase
from email import encoders

email_user = 'alerts@1digitalstack.ai'
email_password = ''
email_send = ['ghansham.pindoriya@1digitalstack.ai','karan.kumar@1digitalstack.ai','arihant.singh@1digitalstack.ai','sambhav.jain@1digitalstack.ai','ankur.dwivedi@1digitalstack.ai','kinshu@1digitalstack.ai']

subject = file
msg = MIMEMultipart()
msg['From'] = email_user
#msg['From'] = "'Abhishek' <{email_user}>"
msg['To'] = ', '.join(email_send)
msg['Subject'] = subject

body = 'Hi,\n\nPFA of today''s mapping request.Please reply as done as you pick this job.'
msg.attach(MIMEText(body,'plain'))

filename=[file]

for file in filename:
    attachment  =open(file,'rb')
    part = MIMEBase('application','octet-stream')
    part.set_payload((attachment).read())
    encoders.encode_base64(part)
    part.add_header('Content-Disposition',"attachment; filename= "+file)
    msg.attach(part)
    text = msg.as_string()

server = smtplib.SMTP('1digitalstack.com',25)
#server.login(email_user,email_password)

server.sendmail(email_user,email_send,text)
server.quit()

(221, b'2.0.0 Bye')

In [ ]:
final

In [ ]:
Url ='https://articulo.mercadolibre.com.mx/MLM-1422791955'

In [ ]:
r= requests.get(Url,headers=headers)
soup=BeautifulSoup(r.content,'html.parser')
main=soup.find('div',class_="ui-pdp-description")
main

In [ ]:
main

In [ ]:
labels=[labels.text for labels in main]
labels


In [ ]:
try:
            main=soup.find('div',class_="ui-pdp-specs__table")
            labels=[labels.text for labels in main.find_all('th')]
            try:
                index=labels.index('Marca')
                value=soup.find_all('td')[index].text
                print(value)
            except:
                value= 'not available'
                print(value)
        except:
            pass

In [ ]:
import pandas as pd
import numpy as np

from selenium import webdriver
from selenium.webdriver.common.by import By
import requests
from selenium.webdriver.support.ui import WebDriverWait
import selenium.webdriver.support.expected_conditions as EC
#from tqdm.notebook import tqdm
from tqdm import tqdm
tqdm.pandas()
import time

In [ ]:
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument("--incognito")
driver = webdriver.Chrome(executable_path = r'C:\Users\Administrator\Desktop\chromedriver.exe',chrome_options = chrome_options)


In [ ]:
link=Url

In [ ]:
        print(link)
        driver.get(link)
        WebDriverWait(driver, timeout).until(EC.visibility_of_element_located((By.ID, locator)))
        